In [1]:
from braindecode.preprocessing import (
    exponential_moving_standardize,
    preprocess,
    Preprocessor)
from numpy import multiply
from braindecode.datasets import MOABBDataset
from braindecode.preprocessing import create_windows_from_events
import torch
from braindecode.util import set_random_seeds

from skorch.callbacks import LRScheduler
from skorch.helper import predefined_split
from braindecode import EEGClassifier
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
import pandas as pd
from sklearn.metrics import confusion_matrix
from braindecode.visualization import plot_confusion_matrix

import numpy as np
import matplotlib.pyplot as plt
import mne
import os
import sys
from mne.datasets import eegbci
import glob
from IPython.display import clear_output
import numpy as np
import torch
from torch import nn
import torch.optim as optim

from mne.datasets import eegbci
from sklearn.model_selection import train_test_split
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader
from scipy import signal


import torch
import torch.cuda as cuda
import torch.nn as nn
from torch.autograd import Variable
import math
import wandb
import os
import neptune.new.integrations.sklearn as npt_utils
import neptune.new as neptune



os.environ['http_proxy'] = "http://192.41.170.23:3128"
os.environ['https_proxy'] = "http://192.41.170.23:3128"

from braindecode.models import ShallowFBCSPNet, Deep4Net ,HybridNet,EEGInceptionMI,EEGITNet,ATCNet

/home/nutapolt/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def create_dataloader(X, y, batch_size):
    X_tensor = torch.tensor(X).float()
    y_tensor = torch.tensor(y).long()
    dataset_tensor = TensorDataset(X_tensor, y_tensor)
    dl = torch.utils.data.DataLoader(dataset_tensor, batch_size=batch_size, shuffle=True)
    return dl

def early_stopping(train_loss, validation_loss, min_delta, tolerance):
    counter = 0
    if (validation_loss - train_loss) > min_delta:
        counter +=1
        if counter >= tolerance:
          return True

def extrack_dataset(dataset):
    for x, y, window_ind in dataset:
        x_shape = x.shape
        y_shape = len(dataset.get_metadata().target)
        break
    X = np.zeros((y_shape,x_shape[0],x_shape[1]))
    y_=[]
    i=0
    for x, y, window_ind in dataset:
        X[i]=x
        y_.append(y)
        i+=1
    #X2 = X[:, 7:8, :]
    #X3= X[:, 11:12, :]
    #(288, 22, 1125)
    #X = np.concatenate((X2,X3), axis=1)
    print(X.shape)

    #X = X.reshape(y_shape,X.shape[2],X.shape[1])
    return X,np.array(y_).T

def extrack_dataset_types(dataset,types = 'NonTarget'):
    for x, y, window_ind in dataset:

        x_shape = x.shape
        y_shape = len(dataset.get_metadata().target)
        break
    X = np.zeros((y_shape,x_shape[0],x_shape[1]))
    y_re = np.zeros(())
    y_=[]
    i=0
    for x, y, window_ind in dataset:
        X[i]=x
        y_.append(y)
        i+=1
    y = np.array(y_).T

    if types == "NonTarget":
        X = X[y == 0]
        y_re = np.zeros((X.shape[0],))
    if types == "Target":
        X = X[y == 1]
        y_re = np.ones((X.shape[0],))
    return X,y_re

def extrack_dataset_2class(dataset):
    for x, y, window_ind in dataset:
        x_shape = x.shape
        y_shape = len(dataset.get_metadata().target)
        break
    X = np.zeros((y_shape,x_shape[0],x_shape[1]))
    y_=[]
    i=0
    for x, y, window_ind in dataset:
        X[i]=x
        y_.append(y)
        i+=1
    y = np.array(y_).T
    X_ = np.zeros((int(y_shape/2) ,x_shape[0],x_shape[1])) #for 2 class
    y_for_2class =[]
    j=0
    for i in range(y.shape[0]):
        if y[i] == 0 or y[i] == 1:
            y_for_2class.append(y[i])
            X_[j]=X[i]
            j +=1
    y_for_2class = np.array(y_for_2class).T
    X_ = X_.reshape(y_for_2class.shape[0],X_.shape[2],X_.shape[1])
    return X_,y_for_2class

def extrack_dataset_2class_cut(dataset):
    for x, y, window_ind in dataset:
        x_shape = x.shape
        y_shape = len(dataset.get_metadata().target)
        break
    X = np.zeros((y_shape,x_shape[0],x_shape[1]))
    y_=[]
    i=0
    for x, y, window_ind in dataset:
        X[i]=x
        y_.append(y)
        i+=1
    y = np.array(y_).T
    X_ = np.zeros((int(y_shape/2) ,x_shape[0],x_shape[1])) #for 2 class
    y_for_2class =[]
    j=0
    for i in range(y.shape[0]):
        if y[i] == 0 or y[i] == 1:
            y_for_2class.append(y[i])
            X_[j]=X[i]
            j +=1
    y_for_2class = np.array(y_for_2class).T
    X_ = X_.reshape(y_for_2class.shape[0],X_.shape[2],X_.shape[1])
    #100, 1, 576, 22
    X_ = X_[:,64:320,:]
    print(X_.shape)
    return X_,y_for_2class


def train(model,gpu_num,train_loader,test_loader,
          weights_name=False,
          optimizer = None,
          criterion = None,
          num_epochs=500,
          vail_loader= None,
          save_weights = False,
          neptune = True,
          lr = None
         ):

    # Train the model


    train_loss = []
    valid_loss = [10,11]
    train_accuracy = []
    valid_accuracy = []

    old_loss = 100
    old_acc = 0
    valid_loss_vail = []


    for epoch in range(num_epochs):
        iter_loss = 0.0
        correct = 0
        iterations = 0

        model.train()

        for i, (items, classes) in enumerate(train_loader):
            items = Variable(items)
            classes = classes.type(torch.LongTensor)
            classes = Variable(classes)

            if cuda.is_available():
                items = items.cuda(gpu_num)
                classes = classes.cuda(gpu_num)

            optimizer.zero_grad()
            outputs = model(items)
            #avg_pedic = torch.mean(outputs, 1, True).float()
            #avg_pedic = avg_pedic.reshape(classes.shape[0])
            #print(avg_pedic.shape)
            #print(classes.shape)
            loss = criterion(outputs, classes)

            iter_loss += loss.item()
            loss.backward()
            optimizer.step()

            metrics = {"train/train_loss": loss}

            #print(loss)
            _, predicted = torch.max(outputs.data, 1)
            correct += (predicted == classes.data).sum()
            iterations += 1

        train_loss.append(iter_loss/iterations)


        train_accuracy.append(( correct.float() / len(train_loader.dataset)))
        train_metrics = {"train/train_loss": iter_loss/iterations,
                       "train/train_accuracy": (100 * correct.float() / len(train_loader.dataset))}



        loss = 0.0
        correct = 0
        iterations = 0

        model.eval()

        for i, (items, classes) in enumerate(test_loader):
            classes = classes.type(torch.LongTensor)
            items = Variable(items)
            classes = Variable(classes)

            if cuda.is_available():
                items = items.cuda(gpu_num)
                classes = classes.cuda(gpu_num)


            outputs = model(items)

            #avg_pedic = torch.mean(outputs, 1, True).float()
            #avg_pedic = avg_pedic.reshape(classes.shape[0])

            loss += criterion(outputs, classes).item()

            _, predicted = torch.max(outputs.data, 1)

            correct += (predicted == classes.data).sum()
            #print("correct : {}".format(classes.data))
            #print("predicted : {}".format(predicted))
            iterations += 1

        valid_loss.append(loss/iterations)
        correct_scalar = np.array([correct.clone().cpu()])[0]
        valid_accuracy.append(correct_scalar / len(test_loader.dataset) )

        test_metrics = {"Test/Test_loss": loss/iterations,
                       "Test/Test_accuracy": correct_scalar / len(test_loader.dataset) }

        if save_weights is True:
            if epoch+1 > 2 and valid_loss[-1] < old_loss and old_acc <= valid_accuracy[-1] :
                    newpath = r'./{}'.format(weights_name)
                    if not os.path.exists(newpath):
                        os.makedirs(newpath)
                    torch.save(model.state_dict(),'./{}/{:.4f}_{}_{:.4f}_{:.4f}'.format(weights_name,valid_loss[-1],weights_name,valid_loss[-1],valid_accuracy[-1]))
                    part_weights = './{}/{:.4f}_{}_{:.4f}_{:.4f}'.format(weights_name,valid_loss[-1],weights_name,valid_loss[-1],valid_accuracy[-1])
                    old_loss = valid_loss[-1]
                    old_acc = valid_accuracy[-1]

        print ('Epoch %d/%d, Tr Loss: %.4f, Tr Acc: %.4f, Val Loss: %.4f, Val Acc: %.4f , le : %f'
                       %(epoch+1, num_epochs, train_loss[-1], train_accuracy[-1], valid_loss[-1], valid_accuracy[-1],lr))
        if early_stopping(train_loss[-1], valid_loss[-1], min_delta=10, tolerance = 20):
            print("We are at epoch:", epoch+1)
            run[f"epoch/valid_accuracy"].append(valid_accuracy[-1])
            run[f"epoch/train_accuracy"].append(train_accuracy[-1])
            run[f"epoch/train_loss"].append(train_loss[-1])
            run[f"epoch/valid_loss"].append(valid_loss[-1])

            break
        if neptune is True:
            run[f"epoch/valid_accuracy"].append(valid_accuracy[-1])
            run[f"epoch/train_accuracy"].append(train_accuracy[-1])
            run[f"epoch/train_loss"].append(train_loss[-1])
            run[f"epoch/valid_loss"].append(valid_loss[-1])
        if epoch+1 == 1:
            stop_loss = valid_loss[-1]

        if  (epoch+1)//500 == 0 and epoch+1 > 1400 :
            if valid_loss[-1] > valid_loss[-500]:
                print("Stop")
                break

    return train_loss,valid_loss,train_accuracy,valid_accuracy,part_weights
def eval(model,
         gpu_num,
          valid_loader= None,
         labels=None,

         ):
    model.eval()
    y_pred = []
    y_true = []
    correct=0
    evaluate_accuracy= []
    for i, (items, classes) in enumerate(valid_loader):
        classes = classes.type(torch.LongTensor)
        items = Variable(items)
        classes = Variable(classes)
        if cuda.is_available():
            items = items.cuda(gpu_num)
            classes = classes.cuda(gpu_num)

        outputs = model(items)
        _, predicted = torch.max(outputs.data, 1)
        y_pred.append(predicted.clone().cpu().numpy())
        y_true.append(classes.data.clone().cpu().numpy())
        correct += (predicted == classes.data).sum()
    correct_scalar = np.array([correct.clone().cpu()])[0]
    evaluate_accuracy.append(correct_scalar / classes.shape[0] )

    confusion_mat = confusion_matrix(np.array(y_true).T,np.array(y_pred).T )
    NonTarget_eva_acc = confusion_mat[0][0]
    Target_eva_acc = confusion_mat[1][1]


    run[f"NonTarget_eva_acc"].append(NonTarget_eva_acc/480)
    run[f"Target_eva_acc"].append(Target_eva_acc/96)



    run[f"epoch/eval_ACC"].append(evaluate_accuracy[-1])
    run["confusion matrices subject_id : {0}".format(subject_id)].upload(plot_confusion_matrix(confusion_mat, class_names=labels,rotate_row_labels=0,rotate_col_labels=90,with_f1_score=True))
    plot_confusion_matrix(confusion_mat, class_names=labels,rotate_row_labels=0,rotate_col_labels=90,with_f1_score=True).savefig('confusion_matrix/confusion matrices subject_id : {2}_{0}_of_{1}.png'.format(subject_id,params['Datasets'],network))
    return y_pred,y_true,correct_scalar,evaluate_accuracy

In [3]:
import numpy as np
from sklearn.metrics import roc_auc_score, precision_score, recall_score, accuracy_score
import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
import torch.nn.functional as F
import torch.optim as optim

class EEGNet(nn.Module):
    def __init__(self):
        super(EEGNet, self).__init__()
        self.T = 1190

        # Layer 1
        self.conv1 = nn.Conv2d(1, 16, (1, 8), padding = 0)
        self.batchnorm1 = nn.BatchNorm2d(16, False)

        # Layer 2
        self.padding1 = nn.ZeroPad2d((16, 17, 0, 1))
        self.conv2 = nn.Conv2d(1, 4, (2, 32))
        self.batchnorm2 = nn.BatchNorm2d(4, False)
        self.pooling2 = nn.MaxPool2d(2, 4)

        # Layer 3
        self.padding2 = nn.ZeroPad2d((2, 1, 4, 3))
        self.conv3 = nn.Conv2d(4, 4, (8, 4))
        self.batchnorm3 = nn.BatchNorm2d(4, False)
        self.pooling3 = nn.MaxPool2d((2, 4))

        # FC Layer
        # NOTE: This dimension will depend on the number of timestamps per sample in your data.
        # I have 120 timepoints.
        self.fc1 = nn.Linear(592, 12)

    def forward(self, x):
        # Layer 1
        x = F.elu(self.conv1(x))
        x = self.batchnorm1(x)
        x = F.dropout(x, 0.25)
        x = x.permute(0, 3, 1, 2)

        # Layer 2
        x = self.padding1(x)
        x = F.elu(self.conv2(x))
        x = self.batchnorm2(x)
        x = F.dropout(x, 0.25)
        x = self.pooling2(x)

        # Layer 3
        x = self.padding2(x)
        x = F.elu(self.conv3(x))
        x = self.batchnorm3(x)
        x = F.dropout(x, 0.25)
        x = self.pooling3(x)

        # FC Layer
        x = x.reshape(x.size(0), -1)
        x = F.sigmoid(self.fc1(x))
        return x


In [4]:
subjects = list(range(1,10))

low_cut_hz = 8.  # low cut frequency for filtering
high_cut_hz = 35.  # high cut frequency for filtering
resample = 250
# Parameters for exponential moving standardization
factor_new = 1e-3
init_block_size = 1000
# Factor to convert from V to uV
factor = 1e6
preprocessors = [
                    Preprocessor('pick_types', eeg=True, meg=False, stim=False),  # Keep EEG sensors
                    Preprocessor(lambda data: multiply(data, factor)),  # Convert from V to uV
                    Preprocessor(exponential_moving_standardize,  # Exponential movin standardization
                                factor_new=factor_new,
                                 init_block_size=init_block_size)
                    ]
n_epochs = 10000
lr = 0.00005

weight_decay = 0.5 * 0.0001

#task_list = ['foot'] ['ATCNet','EEGITNet','ShallowFBCSPNet',]
network_list = ["EEGnet"]
n_classes=2
#network_list = ['Deep4Net']
#percent_list = [72]

gpu_num = 1
session_list = ['session_0']

/home/nutapolt/.local/lib/python3.8/site-packages/braindecode/preprocessing/preprocess.py:55: UserWarning: Preprocessing choices with lambda functions cannot be saved.
  warn('Preprocessing choices with lambda functions cannot be saved.')


In [ ]:
for session in session_list:
    for subject_id in subjects:
        for network in network_list:
            run = neptune.init_run(
    project="AitBrainLab/SSEVP",
    api_token="eyJhcGlfYWRkcmVzcyI6Imh0dHBzOi8vYXBwLm5lcHR1bmUuYWkiLCJhcGlfdXJsIjoiaHR0cHM6Ly9hcHAubmVwdHVuZS5haSIsImFwaV9rZXkiOiJhMTMyMzg0My02NzlhLTQ3N2ItYTdmMS0yNTcwNDBmM2QwM2QifQ==",
    )

            #torch.manual_seed(3407)
            dataset = MOABBDataset(dataset_name="Nakanishi2015", subject_ids= subject_id)
            preprocess(dataset, preprocessors)
            trial_start_offset_seconds = -0.5
            # Extract sampling frequency, check that they are same in all datasets
            sfreq = dataset.datasets[0].raw.info['sfreq']
            print(sfreq)
            assert all([ds.raw.info['sfreq'] == sfreq for ds in dataset.datasets])
            # Calculate the trial start offset in samples.
            trial_start_offset_samples = int(trial_start_offset_seconds * sfreq)

            # Create windows using braindecode function for this. It needs parameters to define how
            # trials should be used.
            windows_dataset = create_windows_from_events(
                dataset,
                trial_start_offset_samples=trial_start_offset_samples,
                trial_stop_offset_samples=0,
                preload=True,
            )
            splitted = windows_dataset.split('session')
            #session_0 = splitted['session_0']
            train_set = splitted[session]

            input_window_samples = train_set[0][0].shape[1]

            #X_train = X_train[:, np.newaxis,:,:]


            X,y = extrack_dataset(train_set)
            print(X.shape)


            if network == "EEGnet":
                X = X.reshape(X.shape[0],X.shape[2],X.shape[1])
                X = X[:, np.newaxis,:,:]


                model = EEGNet()


            X_train, X_valid, y_train, y_valid = train_test_split(X,y, test_size=0.3,stratify=y)

            X_train, X_test, y_train, y_test = train_test_split(X_train,y_train, test_size=0.3,stratify=y_train)

            label_dict = train_set.datasets[0].windows.event_id.items()
            labels = list(dict(sorted(list(label_dict), key=lambda kv: kv[1])).keys())
            print('train size',X_train.shape, y_train.shape)
            print('test size',X_test.shape, y_test.shape)



            train_loader = create_dataloader(X_train, y_train, batch_size=576)
            test_loader = create_dataloader(X_test, y_test, batch_size=576)
            valid_loader = create_dataloader(X_valid, y_valid, batch_size=576)

            n_chans = X_train.shape[1]

            #network_list = ['ATCNet', 'ShallowFBCSPNet', 'Deep4Net', 'EEGNetv4']
            if network == 'ATCNet' :
                model = ATCNet(
                                n_chans,
                                n_classes
                                )
            if network == "ShallowFBCSPNet":
                model = ShallowFBCSPNet(
                n_chans,
                n_classes,
                input_window_samples=input_window_samples,
                final_conv_length="auto",
                )
            if network == "EEGITNet":
                model = EEGITNet(
                    n_classes,
                    n_chans,
                    input_window_samples=input_window_samples,
                    )
            if network == "Deep4Net":
                model = Deep4Net(
                    n_chans,
                    n_classes,
                    input_window_samples=input_window_samples,
                    final_conv_length='auto',
                    n_filters_time=25,
                    n_filters_spat=25,
                    filter_time_length=10,
                    pool_time_length=3,
                    pool_time_stride=3,
                    n_filters_2=50,
                    filter_length_2=10,
                    n_filters_3=100,
                    filter_length_3=10,
                    n_filters_4=200,
                    filter_length_4=10,
                    first_pool_mode="max",
                    later_pool_mode="max",
                    drop_prob=0.5,
                    #double_time_convs=False,
                    split_first_layer=True,
                    batch_norm=True,
                    batch_norm_alpha=0.1,
                    stride_before_pool=False
                    )



            params = {"Subject number":subject_id,
                      "learning_rate": lr ,
                      "optimizer": "AdamW" ,
                      "Network": network,
                      "Datasets":session,
                      "sfreq":dataset.datasets[0].raw.info['sfreq'],
                      "Class number":n_classes,
                      "Channel number": train_set[0][0].shape[0],
                      "samples point" : X_train.shape[2]

                      }
            run["parameters"] = params
            net = model.cuda(gpu_num)
            optimizer = optim.Adam(net.parameters(), lr=lr)
            criterion = nn.CrossEntropyLoss()#nn.BCELoss()#
            train_loss,valid_loss,train_accuracy,valid_accuracy,part_weights =train(
                                                                        model = net,
                                                                        gpu_num = gpu_num,
                                                                        train_loader = train_loader,
                                                                        test_loader = test_loader,
                                                                        optimizer = optimizer  ,
                                                                        criterion = criterion,
                                                                        num_epochs=n_epochs,
                                                                        save_weights= True,
                                                                        lr=lr
                                                                             )
            model.load_state_dict(torch.load(part_weights))
            eval(model = net,
                gpu_num = gpu_num,
                valid_loader= valid_loader,
                 labels=labels,
                 )


            run.stop()

https://app.neptune.ai/AitBrainLab/SSEVP/e/SSEV-9
Remember to stop your run once you’ve finished logging your metadata (https://docs.neptune.ai/api/run#stop). It will be stopped automatically only when the notebook kernel/interactive console is terminated.


Trial data de-meaned and concatenated with a buffer to create continuous data


180 events found
Event IDs: [ 1  2  3  4  5  6  7  8  9 10 11 12]
256.0
Used Annotations descriptions: ['10.25', '10.75', '11.25', '11.75', '12.25', '12.75', '13.25', '13.75', '14.25', '14.75', '9.25', '9.75']
(179, 8, 1190)
(179, 8, 1190)
train size (87, 1, 1190, 8) (87,)
test size (38, 1, 1190, 8) (38,)


/home/nutapolt/.local/lib/python3.8/site-packages/torch/nn/functional.py:1960: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


Epoch 1/10000, Tr Loss: 2.5098, Tr Acc: 0.0575, Val Loss: 2.4880, Val Acc: 0.1053 , le : 0.000050
Epoch 2/10000, Tr Loss: 2.5135, Tr Acc: 0.0460, Val Loss: 2.4878, Val Acc: 0.0789 , le : 0.000050
Epoch 3/10000, Tr Loss: 2.5046, Tr Acc: 0.0690, Val Loss: 2.4823, Val Acc: 0.0789 , le : 0.000050
Epoch 4/10000, Tr Loss: 2.5068, Tr Acc: 0.0575, Val Loss: 2.4827, Val Acc: 0.1053 , le : 0.000050
Epoch 5/10000, Tr Loss: 2.4970, Tr Acc: 0.0805, Val Loss: 2.4848, Val Acc: 0.0526 , le : 0.000050
Epoch 6/10000, Tr Loss: 2.4912, Tr Acc: 0.0805, Val Loss: 2.4755, Val Acc: 0.1053 , le : 0.000050
Epoch 7/10000, Tr Loss: 2.4932, Tr Acc: 0.0690, Val Loss: 2.4791, Val Acc: 0.0526 , le : 0.000050
Epoch 8/10000, Tr Loss: 2.5004, Tr Acc: 0.0920, Val Loss: 2.4894, Val Acc: 0.0789 , le : 0.000050
Epoch 9/10000, Tr Loss: 2.5091, Tr Acc: 0.0575, Val Loss: 2.4898, Val Acc: 0.0526 , le : 0.000050
Epoch 10/10000, Tr Loss: 2.4947, Tr Acc: 0.0690, Val Loss: 2.4834, Val Acc: 0.0526 , le : 0.000050
Epoch 11/10000, Tr 

...

Shutting down background jobs, please wait a moment...
Done!
Waiting for the remaining 20 operations to synchronize with Neptune. Do not kill this process.
All 20 operations synced, thanks for waiting!
Explore the metadata in the Neptune app:
https://app.neptune.ai/AitBrainLab/SSEVP/e/SSEV-12
https://app.neptune.ai/AitBrainLab/SSEVP/e/SSEV-13
Remember to stop your run once you’ve finished logging your metadata (https://docs.neptune.ai/api/run#stop). It will be stopped automatically only when the notebook kernel/interactive console is terminated.


Trial data de-meaned and concatenated with a buffer to create continuous data


180 events found
Event IDs: [ 1  2  3  4  5  6  7  8  9 10 11 12]
256.0
Used Annotations descriptions: ['10.25', '10.75', '11.25', '11.75', '12.25', '12.75', '13.25', '13.75', '14.25', '14.75', '9.25', '9.75']


/home/nutapolt/.local/lib/python3.8/site-packages/torch/nn/functional.py:1960: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


(179, 8, 1190)
(179, 8, 1190)
train size (87, 1, 1190, 8) (87,)
test size (38, 1, 1190, 8) (38,)
Epoch 1/10000, Tr Loss: 2.5014, Tr Acc: 0.0920, Val Loss: 2.4865, Val Acc: 0.0526 , le : 0.000050
Epoch 2/10000, Tr Loss: 2.4911, Tr Acc: 0.0690, Val Loss: 2.4880, Val Acc: 0.1053 , le : 0.000050
Epoch 3/10000, Tr Loss: 2.4961, Tr Acc: 0.0575, Val Loss: 2.4891, Val Acc: 0.1053 , le : 0.000050
Epoch 4/10000, Tr Loss: 2.5159, Tr Acc: 0.1149, Val Loss: 2.4870, Val Acc: 0.1316 , le : 0.000050
Epoch 5/10000, Tr Loss: 2.4950, Tr Acc: 0.0805, Val Loss: 2.4874, Val Acc: 0.1053 , le : 0.000050
Epoch 6/10000, Tr Loss: 2.4849, Tr Acc: 0.0920, Val Loss: 2.4894, Val Acc: 0.1053 , le : 0.000050
Epoch 7/10000, Tr Loss: 2.5048, Tr Acc: 0.0575, Val Loss: 2.4871, Val Acc: 0.1053 , le : 0.000050
Epoch 8/10000, Tr Loss: 2.4972, Tr Acc: 0.0920, Val Loss: 2.4882, Val Acc: 0.1053 , le : 0.000050
Epoch 9/10000, Tr Loss: 2.4950, Tr Acc: 0.0920, Val Loss: 2.4911, Val Acc: 0.1053 , le : 0.000050
Epoch 10/10000, Tr Lo